In [1]:
import os
os.environ["TF_CPP_MIN_LOG_LEVEL"] = "3"           # max silence for TF C++ logs
os.environ["TF_XLA_FLAGS"] = "--tf_xla_auto_jit=0" # disable XLA auto-jit
os.environ["XLA_FLAGS"] = "--xla_gpu_autotune_level=0"
os.chdir("/home/konnilol/Documents/uni/mmo/pr7")

import numpy as np
import pandas as pd

from sklearn.preprocessing import StandardScaler
from sklearn.cluster import KMeans
from sklearn.mixture import GaussianMixture
from sklearn.metrics import silhouette_score, davies_bouldin_score, calinski_harabasz_score

import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers

# Extra silence (Python-side)
tf.get_logger().setLevel("ERROR")
tf.config.optimizer.set_jit(False)  # keep XLA off [web:56]


In [2]:
# -----------------------------
# 1) Load & basic checks
# -----------------------------
df = pd.read_csv("2018-2019_Daily_Attendance_20240429.csv")

# Columns in this file (preview):
# School DBN,Date,Enrolled,Absent,Present,Released [file:112]
df.columns = [c.strip() for c in df.columns]
df = df.rename(columns={"School DBN": "school_dbn"})

# parse date like 20180905
df["Date"] = pd.to_datetime(df["Date"].astype(str), format="%Y%m%d", errors="coerce")
df = df.dropna(subset=["school_dbn", "Date"])

for c in ["Enrolled", "Absent", "Present", "Released"]:
    df[c] = pd.to_numeric(df[c], errors="coerce")

df = df.dropna(subset=["Enrolled", "Absent", "Present", "Released"])

# safe ratios
df["absent_rate"] = df["Absent"] / df["Enrolled"].replace(0, np.nan)
df["present_rate"] = df["Present"] / df["Enrolled"].replace(0, np.nan)
df["released_rate"] = df["Released"] / df["Enrolled"].replace(0, np.nan)
df = df.replace([np.inf, -np.inf], np.nan).dropna(subset=["absent_rate", "present_rate", "released_rate"])


In [3]:
# -----------------------------
# 2) Feature engineering: aggregate per school
#    (so each object = 1 school, features summarize the year)
# -----------------------------
df["dow"] = df["Date"].dt.dayofweek
df["month"] = df["Date"].dt.month

g = df.groupby("school_dbn")

feat = pd.DataFrame({
    "days": g.size(),
    "enrolled_mean": g["Enrolled"].mean(),
    "enrolled_std": g["Enrolled"].std(ddof=0),

    "absent_rate_mean": g["absent_rate"].mean(),
    "absent_rate_std": g["absent_rate"].std(ddof=0),
    "absent_rate_p95": g["absent_rate"].quantile(0.95),

    "present_rate_mean": g["present_rate"].mean(),
    "present_rate_std": g["present_rate"].std(ddof=0),

    "released_rate_mean": g["released_rate"].mean(),
    "released_rate_std": g["released_rate"].std(ddof=0),
}).fillna(0.0)

# weekday seasonality: mean absent_rate per weekday (0..4 useful, but keep 0..6)
dow_mean = df.pivot_table(index="school_dbn", columns="dow", values="absent_rate", aggfunc="mean").fillna(0.0)
dow_mean.columns = [f"absent_rate_dow_{int(c)}" for c in dow_mean.columns]

# monthly seasonality: mean absent_rate per month
month_mean = df.pivot_table(index="school_dbn", columns="month", values="absent_rate", aggfunc="mean").fillna(0.0)
month_mean.columns = [f"absent_rate_month_{int(c)}" for c in month_mean.columns]

X_df = feat.join(dow_mean, how="left").join(month_mean, how="left").fillna(0.0)
schools = X_df.index.to_numpy()
X = X_df.to_numpy(dtype=np.float32)


In [4]:
# -----------------------------
# 3) Utility: internal metrics
# -----------------------------
def clustering_metrics(X_space, labels):
    labels = np.asarray(labels)
    uniq = np.unique(labels)

    # Some methods (e.g., HDBSCAN) could output -1 noise; here we won't use HDBSCAN,
    # but keep robust filtering anyway.
    mask = labels != -1
    if mask.sum() < 3 or len(np.unique(labels[mask])) < 2:
        return {"silhouette": np.nan, "davies_bouldin": np.nan, "calinski_harabasz": np.nan, "n_clusters": int(len(uniq) - (1 if -1 in uniq else 0)), "noise": int((labels == -1).sum())}

    Xv = X_space[mask]
    yv = labels[mask]

    return {
        "silhouette": float(silhouette_score(Xv, yv)),
        "davies_bouldin": float(davies_bouldin_score(Xv, yv)),
        "calinski_harabasz": float(calinski_harabasz_score(Xv, yv)),
        "n_clusters": int(len(np.unique(yv))),
        "noise": int((labels == -1).sum())
    }


In [5]:
# -----------------------------
# 4) (A) Ordinary clustering without normalization
# -----------------------------
K_fixed = 5  # фиксируй одинаково для сравнения "без/с нормализацией"
kmeans_raw = KMeans(n_clusters=K_fixed, n_init=50, random_state=42)
labels_kmeans_raw = kmeans_raw.fit_predict(X)
m_kmeans_raw = clustering_metrics(X, labels_kmeans_raw)



In [6]:
# -----------------------------
# 5) (B) Ordinary clustering with normalization
# -----------------------------
scaler = StandardScaler()
Xn = scaler.fit_transform(X)

kmeans_norm = KMeans(n_clusters=K_fixed, n_init=50, random_state=42)
labels_kmeans_norm = kmeans_norm.fit_predict(Xn)
m_kmeans_norm = clustering_metrics(Xn, labels_kmeans_norm)


In [7]:
# -----------------------------
# 6) (C) Auto number of clusters: GMM + BIC
# -----------------------------
def gmm_select_bic(X_space, k_min=2, k_max=15):
    best = None
    best_bic = np.inf
    bics = []
    Xn64 = X_space.astype(np.float64)
    for k in range(k_min, k_max + 1):
        gmm = GaussianMixture(
            n_components=k,
            covariance_type="diag",   # вместо "full" (часто намного стабильнее) [web:133]
            random_state=42,
            reg_covar=1e-4,           # попробуй 1e-4 или 1e-3 (default 1e-6) [web:133]
            n_init=20,
            init_params="kmeans",
            max_iter=500
        )
        gmm.fit(Xn64)
        bic = gmm.bic(X_space)  # lower better [web:29]
        bics.append((k, float(bic)))
        if bic < best_bic:
            best_bic = bic
            best = gmm
    return best, bics

best_gmm, bics = gmm_select_bic(Xn, k_min=2, k_max=15)
labels_gmm = best_gmm.predict(Xn)
m_gmm = clustering_metrics(Xn, labels_gmm)


In [8]:
# -----------------------------
# 7) (D) Autoencoder then clustering (AE only as representation)
# -----------------------------
in_dim = Xn.shape[1]
latent_dim = 8

inp = keras.Input(shape=(in_dim,))
h = layers.Dense(64, activation="relu")(inp)
h = layers.Dense(32, activation="relu")(h)
z = layers.Dense(latent_dim)(h)

h = layers.Dense(32, activation="relu")(z)
h = layers.Dense(64, activation="relu")(h)
out = layers.Dense(in_dim)(h)

ae = keras.Model(inp, out)
enc = keras.Model(inp, z)
ae.compile(optimizer=keras.optimizers.Adam(1e-3), loss="mse")

cb = [keras.callbacks.EarlyStopping(monitor="val_loss", patience=30, restore_best_weights=True)]

ae.fit(Xn, Xn, validation_split=0.2, epochs=400, batch_size=128, shuffle=True, verbose=0, callbacks=cb)
Z = enc.predict(Xn, batch_size=512, verbose=0)

# cluster in latent with fixed K (fair to compare with KMeans fixed)
kmeans_ae = KMeans(n_clusters=K_fixed, n_init=50, random_state=42)
labels_ae = kmeans_ae.fit_predict(Z)
m_ae = clustering_metrics(Z, labels_ae)


I0000 00:00:1766516969.264102  346991 gpu_device.cc:2020] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 1046 MB memory:  -> device: 0, name: NVIDIA GeForce RTX 3080, pci bus id: 0000:06:00.0, compute capability: 8.6
I0000 00:00:1766516971.843236  348147 device_compiler.h:196] Compiled cluster using XLA!  This line is logged at most once for the lifetime of the process.


In [9]:
# -----------------------------
# 8) (E) Autoencoder + clustering together (DEC-like, fixed K)
#     Here we pick K from GMM+BIC as "some clustering method" partner.
# -----------------------------
K_dec = int(best_gmm.n_components)

# init centers from KMeans on Z
km0 = KMeans(n_clusters=K_dec, n_init=50, random_state=42).fit(Z)
mu = tf.Variable(km0.cluster_centers_.astype("float32"), trainable=True, name="cluster_centers")

alpha = 1.0

def soft_q(z_batch, mu_var):
    z_exp = tf.expand_dims(z_batch, 1)     # (B,1,d)
    mu_exp = tf.expand_dims(mu_var, 0)     # (1,K,d)
    dist_sq = tf.reduce_sum(tf.square(z_exp - mu_exp), axis=2)
    q = 1.0 / (1.0 + dist_sq / alpha)
    q = tf.pow(q, (alpha + 1.0) / 2.0)
    q = q / tf.reduce_sum(q, axis=1, keepdims=True)
    return q

def target_distribution(q_np):
    weight = (q_np ** 2) / np.sum(q_np, axis=0, keepdims=True)
    p = weight / np.sum(weight, axis=1, keepdims=True)
    return p.astype("float32")

def kl_pq(p, q):
    p = tf.clip_by_value(p, 1e-10, 1.0)
    q = tf.clip_by_value(q, 1e-10, 1.0)
    return tf.reduce_mean(tf.reduce_sum(p * tf.math.log(p / q), axis=1))

# build "joint" model that outputs recon and q
inp2 = keras.Input(shape=(in_dim,))
z2 = enc(inp2)
q2 = layers.Lambda(lambda t: soft_q(t, mu))(z2)

h2 = layers.Dense(32, activation="relu")(z2)
h2 = layers.Dense(64, activation="relu")(h2)
recon2 = layers.Dense(in_dim)(h2)

dec_model = keras.Model(inp2, [recon2, q2])

optimizer = keras.optimizers.Adam(1e-4)
mse = keras.losses.MeanSquaredError()

lambda_rec = 1.0
lambda_kl = 0.2
update_interval = 5
max_epochs = 200
batch_size = 128

X_tf = tf.convert_to_tensor(Xn, dtype=tf.float32)
ds = tf.data.Dataset.from_tensor_slices(X_tf).shuffle(len(Xn), seed=42).batch(batch_size)

for epoch in range(1, max_epochs + 1):
    if epoch == 1 or epoch % update_interval == 0:
        _, q_all = dec_model.predict(Xn, batch_size=512, verbose=0)
        P_all = target_distribution(q_all)

    idx = 0
    for xb in ds:
        b = xb.shape[0]
        p_batch = tf.convert_to_tensor(P_all[idx:idx+b], dtype=tf.float32)
        idx += b

        with tf.GradientTape() as tape:
            recon_b, q_b = dec_model(xb, training=True)
            loss = lambda_rec * mse(xb, recon_b) + lambda_kl * kl_pq(p_batch, q_b)

        vars_ = dec_model.trainable_variables + [mu]
        grads = tape.gradient(loss, vars_)
        optimizer.apply_gradients(zip(grads, vars_))

# final labels from DEC
Z_final = enc.predict(Xn, batch_size=512, verbose=0)
_, q_final = dec_model.predict(Xn, batch_size=512, verbose=0)
labels_dec = q_final.argmax(axis=1)
m_dec = clustering_metrics(Z_final, labels_dec)


In [10]:
# -----------------------------
# 9) Collect results, choose best
# -----------------------------
results = pd.DataFrame([
    {"method": "KMeans_raw(no_norm)", **m_kmeans_raw},
    {"method": "KMeans_norm", **m_kmeans_norm},
    {"method": "GMM_BIC(autoK)_norm", **m_gmm},
    {"method": "AE + KMeans(latent)", **m_ae},
    {"method": "AE + DEC(joint) + K_from_BIC", **m_dec},
])

# rank: maximize silhouette & CH, minimize DB
# simple scalarization (z-scores) for convenience
tmp = results.copy()
for c in ["silhouette", "calinski_harabasz"]:
    tmp[c+"_z"] = (tmp[c] - tmp[c].mean()) / (tmp[c].std(ddof=0) + 1e-9)
tmp["davies_bouldin_z"] = (tmp["davies_bouldin"] - tmp["davies_bouldin"].mean()) / (tmp["davies_bouldin"].std(ddof=0) + 1e-9)

tmp["score"] = tmp["silhouette_z"] + tmp["calinski_harabasz_z"] - tmp["davies_bouldin_z"]
results["score"] = tmp["score"]

results = results.sort_values("score", ascending=False).reset_index(drop=True)
print(results)

best_method = results.loc[0, "method"]
print("\nBest method by combined score:", best_method)


                         method  silhouette  davies_bouldin  \
0           KMeans_raw(no_norm)    0.549274        0.507534   
1           AE + KMeans(latent)    0.395990        0.886819   
2                   KMeans_norm    0.363551        0.823814   
3  AE + DEC(joint) + K_from_BIC    0.132816        1.322476   
4           GMM_BIC(autoK)_norm    0.094713        1.688629   

   calinski_harabasz  n_clusters  noise     score  
0        4407.158304           5      0  4.688049  
1        1169.193932           5      0  0.609357  
2        1201.397650           5      0  0.593947  
3         592.221116          14      0 -2.391980  
4         595.264189          14      0 -3.499374  

Best method by combined score: KMeans_raw(no_norm)


In [11]:
# -----------------------------
# 10) Interpret best clustering (top features per cluster)
# -----------------------------
label_map = {
    "KMeans_raw(no_norm)": labels_kmeans_raw,
    "KMeans_norm": labels_kmeans_norm,
    "GMM_BIC(autoK)_norm": labels_gmm,
    "AE + KMeans(latent)": labels_ae,
    "AE + DEC(joint) + K_from_BIC": labels_dec,
}
best_labels = label_map[best_method]

interp = X_df.copy()
interp["cluster"] = best_labels

# mean feature profile per cluster (for interpretation)
profile = interp.groupby("cluster").mean(numeric_only=True)
sizes = interp["cluster"].value_counts().sort_index()
print("\nCluster sizes:\n", sizes)
print("\nCluster mean profile (first 15 cols):\n", profile.iloc[:, :15])



Cluster sizes:
 cluster
0    552
1     19
2     86
3    225
4    701
Name: count, dtype: int64

Cluster mean profile (first 15 cols):
                days  enrolled_mean  enrolled_std  absent_rate_mean  \
cluster                                                              
0        176.259058     568.524607      5.585569          0.085692   
1        167.000000    3618.672426     29.768685          0.084829   
2        175.139535    1587.478184     10.551013          0.063812   
3        176.875556     953.929954      6.523635          0.066268   
4        173.788873     301.056524      5.399093          0.126026   

         absent_rate_std  absent_rate_p95  present_rate_mean  \
cluster                                                        
0               0.044202         0.160628           0.908990   
1               0.042627         0.147778           0.912014   
2               0.031920         0.113709           0.933260   
3               0.035469         0.125050           0

### Вывод: По внутренним метрикам качества лучшей оказалась кластеризация KMeans без нормализации (silhouette 0.549, Davies–Bouldin 0.508, Calinski–Harabasz 4407), а варианты с нормализацией и автоэнкодером дали хуже значения, особенно AE+DEC и GMM+BIC. Полученные кластеры в основном интерпретируются как группы школ, различающиеся по среднему размеру (enrolled_mean) и уровню прогулов (absent_rate_mean), при этом один кластер очень мал (19 объектов), что похоже на группу крупных/нетипичных школ.